## Black Box Interp

### Identity Model

In [45]:
import collections
import copy
import gc
import logging
import math
import os
import pickle
import time
import re

import sys
notebook_dir = os.getcwd()
grandparent_dir = os.path.dirname(os.path.dirname(notebook_dir))
sys.path.append(grandparent_dir)
# sys.path.append('/Users/alanzu/projects/TFs_do_KF_ICL/src/core')
print(sys.path)

import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
import torch
import torch.nn.functional as Fn
from tensordict import TensorDict
from pandas.plotting import table
from datetime import datetime

from core import Config
from models import GPT2, CnnKF
from data_train import set_config_params
from create_plots_with_zero_pred import tf_preds
from linalg_helpers import print_matrix

#set cuda device
os.environ["CUDA_VISIBLE_DEVICES"] = "3"

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
print(f"Using device: {device}")



['/home/sultand/.conda/envs/mop/lib/python312.zip', '/home/sultand/.conda/envs/mop/lib/python3.12', '/home/sultand/.conda/envs/mop/lib/python3.12/lib-dynload', '', '/home/sultand/.local/lib/python3.12/site-packages', '/home/sultand/transformers/src', '/home/sultand/.conda/envs/mop/lib/python3.12/site-packages', '/home/sultand/TFs_do_KF_ICL/src', '/home/sultand/TFs_do_KF_ICL/src', '/home/sultand/TFs_do_KF_ICL/src', '/home/sultand/TFs_do_KF_ICL/src']
Using device: cuda


In [47]:
# get model ckpt

model_name = "ident"

if model_name == "ident":
    valA = "ident"
    valC = "_ident_C"
    nx = 5

ckpt_step = 1500

ckpt_path = f"/data/shared/ICL_Kalman_Experiments/model_checkpoints/GPT2/250124_052617.8dd0f8_multi_sys_trace_ident_state_dim_5_ident_C_lr_1.584893192461114e-05_num_train_sys_40000/checkpoints/step={ckpt_step}.ckpt"

print(ckpt_path)

config = Config()
output_dir, ckpt_dir, experiment_name = set_config_params(config, model_name)

print(f"ckpt_dir: {ckpt_dir}")
config.override("ckpt_path", ckpt_dir + f"/checkpoints/step={ckpt_step}.ckpt")
print(f"ckpt_path: {config.ckpt_path}")

num_gpu = len(config.devices)
batch_size = config.batch_size
print(f"Number of GPUs: {num_gpu}")
print(f"Batch size: {batch_size}")
print(f"Number of training examples: {ckpt_step*batch_size*num_gpu}")

/data/shared/ICL_Kalman_Experiments/model_checkpoints/GPT2/250124_052617.8dd0f8_multi_sys_trace_ident_state_dim_5_ident_C_lr_1.584893192461114e-05_num_train_sys_40000/checkpoints/step=1500.ckpt


IDENTITY MEDIUM MODEL


ckpt_dir: /data/shared/ICL_Kalman_Experiments/model_checkpoints/GPT2/250124_052617.8dd0f8_multi_sys_trace_ident_state_dim_5_ident_C_lr_1.584893192461114e-05_num_train_sys_40000
ckpt_path: /data/shared/ICL_Kalman_Experiments/model_checkpoints/GPT2/250124_052617.8dd0f8_multi_sys_trace_ident_state_dim_5_ident_C_lr_1.584893192461114e-05_num_train_sys_40000/checkpoints/step=1500.ckpt
Number of GPUs: 2
Batch size: 512
Number of training examples: 1536000


In [48]:
#load the model

model = GPT2.load_from_checkpoint(config.ckpt_path,
                                n_dims_in=config.n_dims_in, n_positions=config.n_positions,
                                n_dims_out=config.n_dims_out, n_embd=config.n_embd,
                                n_layer=config.n_layer, n_head=config.n_head, use_pos_emb=config.use_pos_emb, map_location=device, strict=True).eval().to(
    device)

In [49]:
print(f"model: {model}")

model: GPT2(
  (_read_in): Linear(in_features=57, out_features=128, bias=True)
  (_backbone): GPT2Model(
    (wte): Embedding(50257, 128)
    (wpe): Embedding(2048, 128)
    (drop): Dropout(p=0.0, inplace=False)
    (h): ModuleList(
      (0-11): 12 x GPT2Block(
        (ln_1): LayerNorm((128,), eps=1e-05, elementwise_affine=True)
        (attn): GPT2Attention(
          (c_attn): Conv1D(nf=384, nx=128)
          (c_proj): Conv1D(nf=128, nx=128)
          (attn_dropout): Dropout(p=0.0, inplace=False)
          (resid_dropout): Dropout(p=0.0, inplace=False)
        )
        (ln_2): LayerNorm((128,), eps=1e-05, elementwise_affine=True)
        (mlp): GPT2MLP(
          (c_fc): Conv1D(nf=512, nx=128)
          (c_proj): Conv1D(nf=128, nx=512)
          (act): NewGELUActivation()
          (dropout): Dropout(p=0.0, inplace=False)
        )
      )
    )
    (ln_f): LayerNorm((128,), eps=1e-05, elementwise_affine=True)
  )
  (_read_out): Linear(in_features=128, out_features=5, bias=True)
)

In [51]:
#get interleaved test data
num_sys_haystack = 2

config.override("n_positions", num_sys_haystack*12 + 12)


data_path = f"/data/shared/ICL_Kalman_Experiments/train_and_test_data/{valA}/interleaved_traces_{valA}{valC}_state_dim_{nx}_num_sys_haystack_{num_sys_haystack}.pkl"


with open(data_path, "rb") as f:
    data_dict = pickle.load(f)
    for key in data_dict.keys():
        print(f"{key}: {data_dict[key]}\n")

    multi_sys_ys = data_dict["multi_sys_ys"]
    seg_starts_per_config = data_dict["seg_starts_per_config"]

multi_sys_ys: [[[[ 0.          0.          0.         ...  0.          0.
     0.        ]
   [ 0.          0.          0.         ...  0.          0.
     0.        ]
   [ 0.          0.          0.         ...  0.3653136  -1.0134141
     0.7160135 ]
   ...
   [ 0.          0.          0.         ...  0.3653136  -1.0134141
     0.7160135 ]
   [ 0.          0.          0.         ...  0.3653136  -1.0134141
     0.7160135 ]
   [ 0.          0.          0.         ...  0.          0.
     0.        ]]

  [[ 0.          0.          0.         ...  0.          0.
     0.        ]
   [ 0.          0.          0.         ...  0.          0.
     0.        ]
   [ 0.          0.          0.         ... -0.08013932  0.7014316
    -0.3362667 ]
   ...
   [ 0.          0.          0.         ... -0.08013932  0.7014316
    -0.3362667 ]
   [ 0.          0.          0.         ... -0.08013932  0.7014316
    -0.3362667 ]
   [ 0.          0.          0.         ...  0.          0.
     0.        ]]

  

In [58]:
# input data into model


preds_tf = tf_preds(multi_sys_ys, model, device, config)

# print_matrix()
# print(f"preds_tf: {preds_tf[0,0].T.shape}")

trace_config = 0
print(seg_starts_per_config[trace_config])

for trial in range(preds_tf.shape[1]):
    vec1_ind = seg_starts_per_config[trace_config][0] + 1
    vec2_ind = seg_starts_per_config[trace_config][1] + 2

    print(f"vec1_ind: {vec1_ind}, vec2_ind: {vec2_ind}")
    vec1 = multi_sys_ys[trace_config,trial,vec1_ind,-5:]
    vec2 = multi_sys_ys[trace_config,trial,vec2_ind,-5:]

    print_matrix(preds_tf[trace_config,trial].T, f"preds_tf[{trace_config},{trial}].T")
    print_matrix(multi_sys_ys[trace_config,trial,:,-5:].T, f"multi_sys_ys[{trace_config},{trial},:,-5:].T")

    print(f"vec1: {vec1}, vec2: {vec2}\n")

    avg_pred = (vec1 + vec2) / 2

    print(f"avg_pred: {avg_pred}\n")

[1, 13, 25]
vec1_ind: 2, vec2_ind: 15
Matrix preds_tf[0,0].T:
    0.0000     0.2758     0.0012     0.3880     0.3888     0.3894     0.3863     0.3882     0.3928     0.3852     0.3877     0.3840     0.3868     1.7014     0.1633    -0.1739    -0.1729    -0.1747    -0.1759    -0.1710    -0.1742    -0.1773    -0.1710    -0.1782    -0.1759    -0.0073     0.0275     0.3868     0.3910     0.3864     0.3855     0.3891     0.3884     0.3879     0.3931     0.3873     0.3921 
    0.0000     0.2334     0.0176    -0.5247    -0.5175    -0.5164    -0.5137    -0.5114    -0.5135    -0.5125    -0.5106    -0.5096    -0.5085    -0.7746    -0.2720    -0.3685    -0.3692    -0.3695    -0.3716    -0.3671    -0.3699    -0.3727    -0.3710    -0.3691    -0.3720     0.6451    -0.2367    -0.5173    -0.5171    -0.5166    -0.5163    -0.5178    -0.5198    -0.5191    -0.5128    -0.5193    -0.5180 
    0.0000     0.4020    -0.0240     0.3707     0.3651     0.3634     0.3601     0.3640     0.3640     0.3559     0.3622  